####This file only to be used for referencing purposes

In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import warnings
warnings.filterwarnings('ignore')
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from ydata_profiling import ProfileReport
from sklearn.svm import SVR
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.metrics import r2_score, mean_squared_error, mean_absolute_error
import pickle

In [2]:
data = pd.read_csv('Diamond Price prediction.csv')

In [3]:
data

Unnamed: 0  carat        cut color clarity  depth  table  price     x  \
0               1   0.23      Ideal     E     SI2   61.5   55.0    326  3.95   
1               2   0.21    Premium     E     SI1   59.8   61.0    326  3.89   
2               3   0.23       Good     E     VS1   56.9   65.0    327  4.05   
3               4   0.29    Premium     I     VS2   62.4   58.0    334  4.20   
4               5   0.31       Good     J     SI2   63.3   58.0    335  4.34   
...           ...    ...        ...   ...     ...    ...    ...    ...   ...   
53935       53936   0.72      Ideal     D     SI1   60.8   57.0   2757  5.75   
53936       53937   0.72       Good     D     SI1   63.1   55.0   2757  5.69   
53937       53938   0.70  Very Good     D     SI1   62.8   60.0   2757  5.66   
53938       53939   0.86    Premium     H     SI2   61.0   58.0   2757  6.15   
53939       53940   0.75      Ideal     D     SI2   62.2   55.0   2757  5.83   

          y     z  
0      3.98  2.43  
1      3.84  2.31  
2      4.07  2.31  
3      4.23  2.63  
4      4.35  2.75  
...     ...   ...  
53935  5.76  3.50  
53936  5.75  3.61  
53937  5.68  3.56  
53938  6.12  3.74  
53939  5.87  3.64  

[53940 rows x 11 columns]

In [4]:
data.isnull().sum()

Unnamed: 0    0
carat         0
cut           0
color         0
clarity       0
depth         0
table         0
price         0
x             0
y             0
z             0
dtype: int64

In [5]:
data_profile = ProfileReport(data, title = 'Exploratory Data Analysis', explorative = True)

In [6]:
data_profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [7]:
data.drop('Unnamed: 0', axis = 1, inplace =True)

In [8]:
data

carat        cut color clarity  depth  table  price     x     y     z
0       0.23      Ideal     E     SI2   61.5   55.0    326  3.95  3.98  2.43
1       0.21    Premium     E     SI1   59.8   61.0    326  3.89  3.84  2.31
2       0.23       Good     E     VS1   56.9   65.0    327  4.05  4.07  2.31
3       0.29    Premium     I     VS2   62.4   58.0    334  4.20  4.23  2.63
4       0.31       Good     J     SI2   63.3   58.0    335  4.34  4.35  2.75
...      ...        ...   ...     ...    ...    ...    ...   ...   ...   ...
53935   0.72      Ideal     D     SI1   60.8   57.0   2757  5.75  5.76  3.50
53936   0.72       Good     D     SI1   63.1   55.0   2757  5.69  5.75  3.61
53937   0.70  Very Good     D     SI1   62.8   60.0   2757  5.66  5.68  3.56
53938   0.86    Premium     H     SI2   61.0   58.0   2757  6.15  6.12  3.74
53939   0.75      Ideal     D     SI2   62.2   55.0   2757  5.83  5.87  3.64

[53940 rows x 10 columns]

In [9]:
data.cut.unique()

array(['Ideal', 'Premium', 'Good', 'Very Good', 'Fair'], dtype=object)

In [10]:
data.cut.value_counts()

cut
Ideal        21551
Premium      13791
Very Good    12082
Good          4906
Fair          1610
Name: count, dtype: int64

In [11]:
data.color.unique()

array(['E', 'I', 'J', 'H', 'F', 'G', 'D'], dtype=object)

In [12]:
data.color.value_counts()

color
G    11292
E     9797
F     9542
H     8304
D     6775
I     5422
J     2808
Name: count, dtype: int64

In [13]:
data.clarity.unique()

array(['SI2', 'SI1', 'VS1', 'VS2', 'VVS2', 'VVS1', 'I1', 'IF'],
      dtype=object)

In [14]:
data.clarity.value_counts()

clarity
SI1     13065
VS2     12258
SI2      9194
VS1      8171
VVS2     5066
VVS1     3655
IF       1790
I1        741
Name: count, dtype: int64

In [15]:
data.depth.value_counts()

depth
62.0    2239
61.9    2163
61.8    2077
62.2    2039
62.1    2020
        ... 
71.3       1
44.0       1
53.0       1
53.1       1
54.7       1
Name: count, Length: 184, dtype: int64

In [16]:
data.carat.unique()

array([0.23, 0.21, 0.29, 0.31, 0.24, 0.26, 0.22, 0.3 , 0.2 , 0.32, 0.33,
       0.25, 0.35, 0.42, 0.28, 0.38, 0.7 , 0.86, 0.71, 0.78, 0.96, 0.73,
       0.8 , 0.75, 0.74, 0.81, 0.59, 0.9 , 0.91, 0.61, 0.77, 0.63, 0.76,
       0.64, 0.72, 0.79, 0.58, 1.17, 0.6 , 0.83, 0.54, 0.98, 0.52, 1.01,
       0.53, 0.84, 0.51, 1.05, 0.55, 0.87, 1.  , 0.57, 0.82, 1.04, 0.93,
       1.2 , 0.99, 0.34, 0.43, 0.36, 0.95, 0.89, 1.02, 0.97, 0.56, 0.85,
       0.92, 1.27, 0.66, 1.12, 0.68, 1.03, 0.62, 1.22, 1.08, 0.88, 0.5 ,
       1.19, 0.39, 0.65, 1.24, 1.5 , 0.27, 0.41, 1.13, 1.06, 0.69, 0.4 ,
       1.14, 0.94, 1.29, 1.52, 1.16, 1.21, 1.23, 1.09, 0.67, 1.11, 1.1 ,
       1.18, 1.15, 1.25, 1.07, 1.28, 1.51, 0.37, 1.31, 1.26, 1.39, 1.44,
       1.35, 1.3 , 1.32, 1.41, 1.36, 1.45, 1.34, 1.58, 1.54, 1.38, 1.33,
       1.74, 1.64, 1.47, 1.4 , 1.55, 1.95, 2.  , 1.37, 1.83, 1.62, 1.57,
       1.69, 2.06, 1.72, 1.66, 2.14, 1.49, 1.46, 2.15, 1.96, 2.22, 1.7 ,
       1.53, 1.85, 2.01, 2.27, 1.68, 1.56, 1.81, 1.

In [17]:
data.carat.value_counts()

carat
0.30    2604
0.31    2249
1.01    2242
0.70    1981
0.32    1840
        ... 
3.02       1
3.65       1
3.50       1
3.22       1
3.11       1
Name: count, Length: 273, dtype: int64

In [18]:
data

carat        cut color clarity  depth  table  price     x     y     z
0       0.23      Ideal     E     SI2   61.5   55.0    326  3.95  3.98  2.43
1       0.21    Premium     E     SI1   59.8   61.0    326  3.89  3.84  2.31
2       0.23       Good     E     VS1   56.9   65.0    327  4.05  4.07  2.31
3       0.29    Premium     I     VS2   62.4   58.0    334  4.20  4.23  2.63
4       0.31       Good     J     SI2   63.3   58.0    335  4.34  4.35  2.75
...      ...        ...   ...     ...    ...    ...    ...   ...   ...   ...
53935   0.72      Ideal     D     SI1   60.8   57.0   2757  5.75  5.76  3.50
53936   0.72       Good     D     SI1   63.1   55.0   2757  5.69  5.75  3.61
53937   0.70  Very Good     D     SI1   62.8   60.0   2757  5.66  5.68  3.56
53938   0.86    Premium     H     SI2   61.0   58.0   2757  6.15  6.12  3.74
53939   0.75      Ideal     D     SI2   62.2   55.0   2757  5.83  5.87  3.64

[53940 rows x 10 columns]

In [19]:
cut = pd.get_dummies(data.cut, dtype = int)

In [20]:
cut

Fair  Good  Ideal  Premium  Very Good
0         0     0      1        0          0
1         0     0      0        1          0
2         0     1      0        0          0
3         0     0      0        1          0
4         0     1      0        0          0
...     ...   ...    ...      ...        ...
53935     0     0      1        0          0
53936     0     1      0        0          0
53937     0     0      0        0          1
53938     0     0      0        1          0
53939     0     0      1        0          0

[53940 rows x 5 columns]

In [21]:
color = pd.get_dummies(data.color, dtype=int)

In [22]:
color

D  E  F  G  H  I  J
0      0  1  0  0  0  0  0
1      0  1  0  0  0  0  0
2      0  1  0  0  0  0  0
3      0  0  0  0  0  1  0
4      0  0  0  0  0  0  1
...   .. .. .. .. .. .. ..
53935  1  0  0  0  0  0  0
53936  1  0  0  0  0  0  0
53937  1  0  0  0  0  0  0
53938  0  0  0  0  1  0  0
53939  1  0  0  0  0  0  0

[53940 rows x 7 columns]

In [23]:
clarity = pd.get_dummies(data.clarity, dtype = int)

In [24]:
clarity

I1  IF  SI1  SI2  VS1  VS2  VVS1  VVS2
0       0   0    0    1    0    0     0     0
1       0   0    1    0    0    0     0     0
2       0   0    0    0    1    0     0     0
3       0   0    0    0    0    1     0     0
4       0   0    0    1    0    0     0     0
...    ..  ..  ...  ...  ...  ...   ...   ...
53935   0   0    1    0    0    0     0     0
53936   0   0    1    0    0    0     0     0
53937   0   0    1    0    0    0     0     0
53938   0   0    0    1    0    0     0     0
53939   0   0    0    1    0    0     0     0

[53940 rows x 8 columns]

In [25]:
data = pd.concat([cut,color,clarity,data], axis = 1)

In [26]:
data

Fair  Good  Ideal  Premium  Very Good  D  E  F  G  H  ...  carat  \
0         0     0      1        0          0  0  1  0  0  0  ...   0.23   
1         0     0      0        1          0  0  1  0  0  0  ...   0.21   
2         0     1      0        0          0  0  1  0  0  0  ...   0.23   
3         0     0      0        1          0  0  0  0  0  0  ...   0.29   
4         0     1      0        0          0  0  0  0  0  0  ...   0.31   
...     ...   ...    ...      ...        ... .. .. .. .. ..  ...    ...   
53935     0     0      1        0          0  1  0  0  0  0  ...   0.72   
53936     0     1      0        0          0  1  0  0  0  0  ...   0.72   
53937     0     0      0        0          1  1  0  0  0  0  ...   0.70   
53938     0     0      0        1          0  0  0  0  0  1  ...   0.86   
53939     0     0      1        0          0  1  0  0  0  0  ...   0.75   

             cut  color  clarity  depth  table  price     x     y     z  
0          Ideal      E      SI2   61.5   55.0    326  3.95  3.98  2.43  
1        Premium      E      SI1   59.8   61.0    326  3.89  3.84  2.31  
2           Good      E      VS1   56.9   65.0    327  4.05  4.07  2.31  
3        Premium      I      VS2   62.4   58.0    334  4.20  4.23  2.63  
4           Good      J      SI2   63.3   58.0    335  4.34  4.35  2.75  
...          ...    ...      ...    ...    ...    ...   ...   ...   ...  
53935      Ideal      D      SI1   60.8   57.0   2757  5.75  5.76  3.50  
53936       Good      D      SI1   63.1   55.0   2757  5.69  5.75  3.61  
53937  Very Good      D      SI1   62.8   60.0   2757  5.66  5.68  3.56  
53938    Premium      H      SI2   61.0   58.0   2757  6.15  6.12  3.74  
53939      Ideal      D      SI2   62.2   55.0   2757  5.83  5.87  3.64  

[53940 rows x 30 columns]

In [27]:
data.drop(['cut','color','clarity'], axis = 1, inplace = True)

In [28]:
data

Fair  Good  Ideal  Premium  Very Good  D  E  F  G  H  ...  VS2  VVS1  \
0         0     0      1        0          0  0  1  0  0  0  ...    0     0   
1         0     0      0        1          0  0  1  0  0  0  ...    0     0   
2         0     1      0        0          0  0  1  0  0  0  ...    0     0   
3         0     0      0        1          0  0  0  0  0  0  ...    1     0   
4         0     1      0        0          0  0  0  0  0  0  ...    0     0   
...     ...   ...    ...      ...        ... .. .. .. .. ..  ...  ...   ...   
53935     0     0      1        0          0  1  0  0  0  0  ...    0     0   
53936     0     1      0        0          0  1  0  0  0  0  ...    0     0   
53937     0     0      0        0          1  1  0  0  0  0  ...    0     0   
53938     0     0      0        1          0  0  0  0  0  1  ...    0     0   
53939     0     0      1        0          0  1  0  0  0  0  ...    0     0   

       VVS2  carat  depth  table  price     x     y     z  
0         0   0.23   61.5   55.0    326  3.95  3.98  2.43  
1         0   0.21   59.8   61.0    326  3.89  3.84  2.31  
2         0   0.23   56.9   65.0    327  4.05  4.07  2.31  
3         0   0.29   62.4   58.0    334  4.20  4.23  2.63  
4         0   0.31   63.3   58.0    335  4.34  4.35  2.75  
...     ...    ...    ...    ...    ...   ...   ...   ...  
53935     0   0.72   60.8   57.0   2757  5.75  5.76  3.50  
53936     0   0.72   63.1   55.0   2757  5.69  5.75  3.61  
53937     0   0.70   62.8   60.0   2757  5.66  5.68  3.56  
53938     0   0.86   61.0   58.0   2757  6.15  6.12  3.74  
53939     0   0.75   62.2   55.0   2757  5.83  5.87  3.64  

[53940 rows x 27 columns]

In [29]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 53940 entries, 0 to 53939
Data columns (total 27 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   Fair       53940 non-null  int32  
 1   Good       53940 non-null  int32  
 2   Ideal      53940 non-null  int32  
 3   Premium    53940 non-null  int32  
 4   Very Good  53940 non-null  int32  
 5   D          53940 non-null  int32  
 6   E          53940 non-null  int32  
 7   F          53940 non-null  int32  
 8   G          53940 non-null  int32  
 9   H          53940 non-null  int32  
 10  I          53940 non-null  int32  
 11  J          53940 non-null  int32  
 12  I1         53940 non-null  int32  
 13  IF         53940 non-null  int32  
 14  SI1        53940 non-null  int32  
 15  SI2        53940 non-null  int32  
 16  VS1        53940 non-null  int32  
 17  VS2        53940 non-null  int32  
 18  VVS1       53940 non-null  int32  
 19  VVS2       53940 non-null  int32  
 20  carat 

In [30]:
scaling = StandardScaler()

In [31]:
scaled_data = ['carat','depth','price','table','x','y','z']

In [32]:
data[scaled_data] = scaling.fit_transform(data[scaled_data])

In [33]:
data

Fair  Good  Ideal  Premium  Very Good  D  E  F  G  H  ...  VS2  VVS1  \
0         0     0      1        0          0  0  1  0  0  0  ...    0     0   
1         0     0      0        1          0  0  1  0  0  0  ...    0     0   
2         0     1      0        0          0  0  1  0  0  0  ...    0     0   
3         0     0      0        1          0  0  0  0  0  0  ...    1     0   
4         0     1      0        0          0  0  0  0  0  0  ...    0     0   
...     ...   ...    ...      ...        ... .. .. .. .. ..  ...  ...   ...   
53935     0     0      1        0          0  1  0  0  0  0  ...    0     0   
53936     0     1      0        0          0  1  0  0  0  0  ...    0     0   
53937     0     0      0        0          1  1  0  0  0  0  ...    0     0   
53938     0     0      0        1          0  0  0  0  0  1  ...    0     0   
53939     0     0      1        0          0  1  0  0  0  0  ...    0     0   

       VVS2     carat     depth     table     price         x         y  \
0         0 -1.198168 -0.174092 -1.099672 -0.904095 -1.587837 -1.536196   
1         0 -1.240361 -1.360738  1.585529 -0.904095 -1.641325 -1.658774   
2         0 -1.198168 -3.385019  3.375663 -0.903844 -1.498691 -1.457395   
3         0 -1.071587  0.454133  0.242928 -0.902090 -1.364971 -1.317305   
4         0 -1.029394  1.082358  0.242928 -0.901839 -1.240167 -1.212238   
...     ...       ...       ...       ...       ...       ...       ...   
53935     0 -0.164427 -0.662711 -0.204605 -0.294731  0.016798  0.022304   
53936     0 -0.164427  0.942753 -1.099672 -0.294731 -0.036690  0.013548   
53937     0 -0.206621  0.733344  1.137995 -0.294731 -0.063434 -0.047741   
53938     0  0.130927 -0.523105  0.242928 -0.294731  0.373383  0.337506   
53939     0 -0.101137  0.314528 -1.099672 -0.294731  0.088115  0.118616   

              z  
0     -1.571129  
1     -1.741175  
2     -1.741175  
3     -1.287720  
4     -1.117674  
...         ...  
53935 -0.054888  
53936  0.100988  
53937  0.030135  
53938  0.285204  
53939  0.143499  

[53940 rows x 27 columns]

In [37]:
data.loc[data["carat"]== "scatter carat, carat"]

Empty DataFrame
Columns: [Fair, Good, Ideal, Premium, Very Good, D, E, F, G, H, I, J, I1, IF, SI1, SI2, VS1, VS2, VVS1, VVS2, carat, depth, table, price, x, y, z]
Index: []

[0 rows x 27 columns]

In [38]:
X = data.drop('price', axis = 1)
y = data.price

In [39]:
X_train, X_test, y_train, y_test = train_test_split(X,y, test_size = 0.3, random_state = 42)

In [40]:
model = SVR()

model.fit(X_train, y_train)

SVR()

In [41]:
y_pred = model.predict(X_test)

In [42]:
r2_score(y_test,y_pred)

0.9779662682638254

In [43]:
mean_squared_error(y_test,y_pred)

0.021591583622765757

In [44]:
mean_absolute_error(y_test,y_pred)

0.08442587862221491

In [ ]:
#Create your own pickle file as required
pickle.dump(model,open('svrmodel.pkl','wb'))